# Generate BitMasks

The purpose of this notebook is to generate bitmasks to be used as filters, using the BAMBOO algorithm.

In [1]:
def generate_bitmaps(
    total_length: str, mask_length: str, mask_characters_list: list
) -> list:
    if total_length % mask_length != 0:
        raise ValueError(f"Total length must be a multiple of {mask_length}.")

    num_bitmaps = total_length // mask_length

    bitmaps = [
        "0" * (i * mask_length)
        + mask_characters_list[0] * (mask_length // 2)
        + mask_characters_list[1] * (mask_length // 2)
        + "0" * ((num_bitmaps - i - 1) * mask_length)
        for i in range(num_bitmaps)
    ]
    return bitmaps

In [2]:
total_length = 1024
mask_length = 8
mask_characters = ["1", "-1"]
bitmaps = generate_bitmaps(total_length, mask_length, mask_characters)
for bitmap in bitmaps:
    print(bitmap)

1111-1-1-1-10000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000

In [5]:
def generate_bitmask_filters_with_mixed_patterns(L, lengths=[4, 8, 16]):
    filters = []

    def create_patterns(length):
        """Helper function to create mixed patterns of 1s and -1s"""
        patterns = []

        # Generate all possible patterns with 1s and -1s for the given length
        for i in range(1 << length):
            pattern = []
            for j in range(length):
                if i & (1 << j):
                    pattern.append(1)
                else:
                    pattern.append(-1)
            patterns.append(pattern)

        return patterns

    for length in lengths:
        num_windows = L // length  # Number of full windows we can fit in L

        for i in range(num_windows):
            # Create a base mask of 0s with length `L`
            base_mask = [0] * L

            # Define the position of the window
            start_pos = i * length
            end_pos = start_pos + length

            # Get all mixed patterns for the current window length
            patterns = create_patterns(length)

            for pattern in patterns:
                # Create a mask with the current pattern
                mask = base_mask[:]

                for j in range(length):
                    if start_pos + j < L:
                        mask[start_pos + j] = pattern[j]

                # Convert the mask list to a string
                filters.append("".join(map(str, mask)))

    return filters


# Example usage:
L = 32
bitmask_filters = generate_bitmask_filters_with_mixed_patterns(L)
for f in bitmask_filters:
    print(f)

-1-1-1-10000000000000000000000000000
1-1-1-10000000000000000000000000000
-11-1-10000000000000000000000000000
11-1-10000000000000000000000000000
-1-11-10000000000000000000000000000
1-11-10000000000000000000000000000
-111-10000000000000000000000000000
111-10000000000000000000000000000
-1-1-110000000000000000000000000000
1-1-110000000000000000000000000000
-11-110000000000000000000000000000
11-110000000000000000000000000000
-1-1110000000000000000000000000000
1-1110000000000000000000000000000
-11110000000000000000000000000000
11110000000000000000000000000000
0000-1-1-1-1000000000000000000000000
00001-1-1-1000000000000000000000000
0000-11-1-1000000000000000000000000
000011-1-1000000000000000000000000
0000-1-11-1000000000000000000000000
00001-11-1000000000000000000000000
0000-111-1000000000000000000000000
0000111-1000000000000000000000000
0000-1-1-11000000000000000000000000
00001-1-11000000000000000000000000
0000-11-11000000000000000000000000
000011-11000000000000000000000000
0000-1-111000000

In [6]:
len(bitmask_filters)

132224

In [10]:
def generate_specific_bitmask_patterns(L, lengths=[4, 8, 16]):
    filters = []

    def create_specific_patterns(length):
        """Helper function to create specific patterns"""
        half_len = length // 2

        # Pattern 1: First half -1, last half 1
        pattern1 = [-1] * half_len + [1] * (length - half_len)

        # Pattern 2: First half 1, last half -1
        pattern2 = [1] * half_len + [-1] * (length - half_len)

        # Pattern 3: All 1
        pattern3 = [1] * length

        # Pattern 4: All -1
        pattern4 = [-1] * length

        # Pattern 5: Alternating -1 and 1
        pattern5 = [(-1) ** i for i in range(length)]

        # Pattern 6: Alternating 1 and -1
        pattern6 = [1 if i % 2 == 0 else -1 for i in range(length)]

        return [pattern1, pattern2, pattern3, pattern4, pattern5, pattern6]

    for length in lengths:
        num_windows = L // length  # Number of full windows we can fit in L

        for i in range(num_windows):
            # Create a base mask of 0s with length `L`
            base_mask = [0] * L

            # Define the position of the window
            start_pos = i * length
            end_pos = start_pos + length

            # Get all specific patterns for the current window length
            patterns = create_specific_patterns(length)

            for pattern in patterns:
                # Create a mask with the current pattern
                mask = base_mask[:]

                for j in range(length):
                    if start_pos + j < L:
                        mask[start_pos + j] = pattern[j]

                # Convert the mask list to a string
                filters.append("".join(map(str, mask)))

    return filters


# Example usage:
L = 1024
bitmask_filters = generate_specific_bitmask_patterns(L)
for f in bitmask_filters:
    print(f)

-1-1110000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000000

In [11]:
len(bitmask_filters)

2240